In [1]:
import os, sumolib
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn3
from datetime import datetime

In [2]:
class DailyPreprocessor:
    def __init__(self, config_name='revised', nowTime=datetime.now()):
        self.config_name = config_name
        self.nowTime = nowTime
self = DailyPreprocessor(nowTime = datetime.now())

In [3]:
## 교차로목록 정의
sixties = pd.read_excel('교차로기반정보_(시범지역).xlsx', header=1)
self.inter_nos = set(sixties['교차로 ID'].dropna().astype(int))
# 551, 561은 TC_IF_TOD_RED_YELLO, TN_IF_SIGL_FLOW에 존재하지 않음. TOD 보고서에서도 확인할 수 없음
# 551 : 보육시설 삼거리, 561 : 공영주차장 단일로
self.inter_nos = self.inter_nos - {551, 561}
# 464는 매칭테이블에 존재하지 않음. 500에 매칭되는 node_id가 네트워크에 존재하지 않음.
# 464 : 성남공판장 단일로, 500 : 단남아파트 단일로
self.inter_nos = self.inter_nos - {464, 500}
print(len(self.inter_nos))
inter_nos_display = ", ".join(map(str, sorted(self.inter_nos)))
inter_nos_display = "\n".join([inter_nos_display[i:i+100] for i in range(0, len(inter_nos_display), 100)])
# print(len(inter_nos_display))
print(inter_nos_display)

56
436, 437, 438, 442, 443, 444, 455, 456, 457, 458, 459, 460, 461, 462, 463, 472, 474, 482, 483, 484, 
485, 486, 488, 490, 491, 492, 493, 494, 498, 499, 502, 503, 504, 514, 515, 523, 524, 527, 565, 575, 
576, 581, 582, 583, 611, 615, 631, 632, 633, 634, 635, 636, 637, 638, 639, 640


In [4]:
## 매칭테이블 정의, 교차로-노드 딕셔너리 정의
self.net = sumolib.net.readNet('new_sungnam_network_internal_0809.net.xml')
self.inter_node = pd.read_excel('signal_node_matching.xlsx', dtype={'node_id':str})
self.inter_node = self.inter_node.rename(columns={'signal_id':'inter_no'})
self.inter_node['inter_type'] = 'parent'
self.inter_node = self.inter_node[self.inter_node.inter_no.isin(self.inter_nos)].reset_index(drop=True)

# 일대일대응 확인
if not len(self.inter_node) == self.inter_node.inter_no.nunique() == self.inter_node.node_id.nunique():
    raise ValueError("Warning: 'inter_no'와 'node_id' 간에 일대일대응 관계가 성립하지 않습니다.")

# 교차로번호 vs 노드id 간 딕셔너리
self.inter2node = dict(zip(self.inter_node.inter_no, self.inter_node.node_id))
self.node2inter = dict(zip(self.inter_node.node_id, self.inter_node.inter_no))
self.node_ids = {self.inter2node[inter_no] for inter_no in self.inter_nos}

In [5]:
# net = sumolib.net.readNet('new_sungnam_network_internal_0809.net.xml')
# inter_node = pd.read_excel('signal_node_matching.xlsx', dtype={'node_id':str})
# print(len(set(inter_node.signal_id)))
# print(inter_nos - set(inter_node.signal_id))
# inter_node = inter_node[inter_node.node_id.isin(node.getID() for node in net.getNodes())]
# print(len(set(inter_node.signal_id)))
# print(inter_nos - set(inter_node.signal_id))

In [6]:
## 테이블 표준화

# 주요 테이블 로드 (실제로는 쿼리문 작성 부분이 되어야 함.)
self.dayplan  = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_DAY_PLAN.csv'))
self.holyplan = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_HOLIDAY_PLAN.csv'))
self.red_yel  = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_RED_YELLO.csv'))
self.weekplan = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TC_IF_TOD_WEEK_PLAN.csv'))
# 교차로정보 테이블은 불러오지 않음 (해당 테이블이 실질적으로 쓰이지는 않고, 60개 테이블 정보가 있지도 않음)
# inter_info=pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TM_FA_CRSRD.csv'))
self.flows    = pd.read_csv(os.path.join(os.path.abspath('.'), 'sn_admin_tables', 'TN_IF_SIGL_FLOW.csv'))

# 유효한 교차로들에 대하여만 슬라이싱
self.dayplan = self.dayplan[self.dayplan.CRSRD_ID.isin(self.inter_nos)]
self.weekplan= self.weekplan[self.weekplan.CRSRD_ID.isin(self.inter_nos)]
self.red_yel = self.red_yel[self.red_yel.CRSRD_ID.isin(self.inter_nos)]
self.flows   = self.flows[self.flows.CRSRD_ID.isin(self.inter_nos)]

# 컬럼명 변경 적용
rename_cname_1 = {'CRSRD_ID':'inter_no',        'CYCL':'cycle',             'DAY':'DD',
                  'HOUR':'hh',                  'MIN':'mm',                 'MNTH':'MM',
                  'OFFSET':'offset',            'PHASE':'phase_no',         'PLAN_NO':'plan_no',
                  'RINGA_RED_SEC':'red_A',      'RINGA_YELLO_SEC':'yel_A',  'RINGB_RED_SEC':'red_B',
                  'RINGB_YELLO_SEC':'yel_B'}

rename_cname_2 = {f'RING{alph}_PHASE{i}':f'dura_{alph}{i}' for alph in ['A', 'B'] for i in range(1,9)}
rename_cname = {**rename_cname_1, **rename_cname_2}
self.dayplan  = self.dayplan.rename(columns=rename_cname)
self.holyplan = self.holyplan.rename(columns=rename_cname)
self.weekplan = self.weekplan.rename(columns=rename_cname)
self.red_yel  = self.red_yel.rename(columns=rename_cname)


In [7]:
## self.plan : 신호계획 테이블 생성

# 날짜, 요일 지정
MM, DD = self.nowTime.month, self.nowTime.day # 날짜
dow_number = self.nowTime.weekday() # 요일
hplan = self.holyplan[(self.holyplan.MM==MM) & (self.holyplan.DD==DD)]
dows = [dow for dow in self.weekplan.columns if dow.endswith('PLAN_NO')]
dows = dows[1:] + dows[0:1]
dow = dows[dow_number]

# (신호교차로, 신호계획번호) 목록
if len(hplan):
    inter_pnos = list(zip(hplan['inter_no'], hplan['plan_no']))
else:
    inter_pnos = list(zip(self.weekplan.inter_no, self.weekplan[dow]))

# 신호테이블 통합
self.plan = self.dayplan.copy()
self.plan['inter_pno'] = list(zip(self.plan['inter_no'], self.plan['plan_no']))
self.plan = self.plan[(self.plan.inter_pno.isin(inter_pnos))]
self.plan = self.plan.drop(columns='inter_pno')
max_phase_no = int(self.red_yel.phase_no.max())
for j in range(1,max_phase_no+1):
    RY = self.red_yel[self.red_yel.phase_no==j].iloc[0]
    red_A = RY.red_A
    red_B = RY.red_B
    yel_A = RY.yel_A
    yel_B = RY.yel_B
    self.plan[f'red_A{j}'] = red_A
    self.plan[f'red_B{j}'] = red_B
    self.plan[f'yellow_A{j}'] = yel_A
    self.plan[f'yellow_B{j}'] = yel_B

In [8]:
## self.angle : 각도(이동류방향) 테이블 생성
self.angle = self.flows.copy()
self.angle = self.angle.rename(columns={'CRSRD_ID':'inter_no',    'PHASE':'phase_no',
                              'RING':'ring_type',       'FLOW_NO':'move_no'})
# 유효한 이동류번호 및 교차로번호로 슬라이싱
self.angle = self.angle[self.angle.move_no.isin(range(1,19))]
self.angle = self.angle[self.angle.inter_no.isin(self.inter_nos)]
# 세 점 데이터 파싱 및 각도코드 열 생성
for ind, row in self.angle.iterrows():
    arrow = row.SIGL_ARROW
    # 위경도 추출
    # arrow = re.findall(r'-?\d+\.?\d*', arrow)
    arrow = [coord.lstrip(' ') for coord in arrow.split(',')]
    arrow = [coord.lstrip('[') for coord in arrow]
    arrow = [coord.rstrip(']') for coord in arrow]
    exists = all([bool(coord) for coord in arrow])
    if exists:
        y1, x1, y2, x2, y3, x3 = arrow

        # 미터 단위로 변환
        x1, y1 = self.net.convertLonLat2XY(x1, y1)
        x2, y2 = self.net.convertLonLat2XY(x2, y2)
        x3, y3 = self.net.convertLonLat2XY(x3, y3)

        # 진입각, 진출각 설정
        inc_angle = np.arctan2(y1 - y2, x1 - x2)
        out_angle = np.arctan2(y3 - y2, x3 - x2)
        inc_angle = inc_angle * 180 / np.pi
        out_angle = out_angle * 180 / np.pi
        inc_angle = int((90 - inc_angle) % 360)
        out_angle = int((90 - out_angle) % 360)

        # 각도코드 설정
        angle_code = str(inc_angle).zfill(3) + str(out_angle).zfill(3)
        # print(angle_code)
        self.angle.loc[ind, 'angle_code'] = angle_code
    else:
        self.angle.loc[ind, 'angle_code'] = None
self.angle = self.angle.drop(columns='SIGL_ARROW')
self.angle = self.angle.reset_index(drop=True)\
    .sort_values(by=['inter_no', 'phase_no', 'ring_type']).reset_index(drop=True)
self.angle

inter_no  phase_no ring_type  move_no  STOS_NO angle_code
0         436         1         A        5        0     262358
1         436         1         B        2        0     262074
2         436         2         A        8        0     174355
3         436         2         B        3        0     172263
4         436         3         A        7        0     356074
..        ...       ...       ...      ...      ...        ...
371       639         4         A        6        0     120312
372       639         4         B        1        0     126221
373       640         1         A        8        0     226052
374       640         1         B        4        0     043222
375       640         2         A       17        0       None

[376 rows x 6 columns]

In [13]:
## self.match1 테이블 생성
match1 = self.flows.copy()
match1 = match1[['CRSRD_ID', 'PHASE', 'RING', 'FLOW_NO']]
match1 = match1.rename(columns={'CRSRD_ID':'inter_no',  'PHASE':'phase_no', 'RING':'ring_type', 'FLOW_NO':'move_no'})
match1 = match1.sort_values(by=['inter_no', 'phase_no', 'ring_type']).reset_index(drop=True)
# 유효한 이동류번호 및 교차로번호로 슬라이싱
match1 = match1[match1.move_no.isin(range(1,19))]
match1 = match1[match1.inter_no.isin(self.inter_nos)]
# 특정한 (교차로번호, 현시번호)에 대하여 한 링에 대해서만 이동류번호만 정의된 경우, 나머지 링에 대해서 이동류 정의
additional_m1s = []
for key, group in match1.groupby(['inter_no', 'phase_no']):
    inter_no, phase_no = map(int,key)
    if set(group.ring_type) != {'A', 'B'}:
        assert len(group)==1
        ring_type = group.iloc[0].ring_type
        RING_TYPE = list({'A', 'B'} - set(ring_type))[0]
        additional_m1 = group.copy()
        additional_m1['ring_type'] = RING_TYPE
        additional_m1s.append(additional_m1)
match1 = pd.concat([match1] + additional_m1s)
match1 = match1.reset_index(drop=True)
display(match1)
# 열 재편 : 현시시간과 이동류번호 열을 A, B로 구분
match1s = []
for key, group in match1.copy().groupby(['inter_no', 'phase_no']):
    inter_no, phase_no = map(int, key)
    assert len(group) == 2
    row_A = group[group.ring_type=='A']
    row_B = group[group.ring_type=='B']
    assert len(row_A)==len(row_B)==1
    row_A = row_A.iloc[0]
    row_B = row_B.iloc[0]
    m1 = pd.DataFrame({'inter_no':[inter_no], 'phas_A':[phase_no], 'phas_B':[phase_no],
                       'move_A':[row_A.move_no], 'move_B':[row_B.move_no]})
    match1s.append(m1)
display(match1)
self.match1 = pd.concat(match1s).reset_index(drop=True)

inter_no  phase_no ring_type  move_no
0         436         1         A        5
1         436         1         B        2
2         436         2         A        8
3         436         2         B        3
4         436         3         A        7
..        ...       ...       ...      ...
383       576         2         B       17
384       582         2         B       17
385       632         2         B       17
386       634         4         B        5
387       640         2         B       17

[388 rows x 4 columns]

inter_no  phase_no ring_type  move_no
0         436         1         A        5
1         436         1         B        2
2         436         2         A        8
3         436         2         B        3
4         436         3         A        7
..        ...       ...       ...      ...
383       576         2         B       17
384       582         2         B       17
385       632         2         B       17
386       634         4         B        5
387       640         2         B       17

[388 rows x 4 columns]

In [10]:
# # self.coord : 연등교차로 테이블 생성
# self.coord = pd.DataFrame(columns=['parent_id', 'child_id', 'phase_no', 'ring_type', 'inc_edge_id', 'out_edge_id'])

Empty DataFrame
Columns: [parent_id, child_id, phase_no, ring_type, inc_edge_id, out_edge_id]
Index: []

In [11]:
self.inter_node

inter_no node_id inter_type
0        436  109836     parent
1        437  109986     parent
2        438  106350     parent
3        442  106332     parent
4        443  108769     parent
5        444  109842     parent
6        455  109901     parent
7        456  106231     parent
8        457  106234     parent
9        458  106238     parent
10       459  106242     parent
11       460  109946     parent
12       461  109829     parent
13       462  106174     parent
14       463  106267     parent
15       472  109965     parent
16       474  109845     parent
17       482  106329     parent
18       483  107928     parent
19       484  106303     parent
20       485  107940     parent
21       486  106273     parent
22       488  107093     parent
23       490  106908     parent
24       491  109987     parent
25       492  106244     parent
26       493  106225     parent
27       494  108235     parent
28       498  107120     parent
29       499  107111     parent
30       502  106286     parent
31       503  106313     parent
32       504  109897     parent
33       514  106708     parent
34       515  106969     parent
35       523  106325     parent
36       524  107049     parent
37       527  107123     parent
38       565  109943     parent
39       575  106197     parent
40       576  107955     parent
41       581  106326     parent
42       582  108639     parent
43       583  106184     parent
44       611  107345     parent
45       615  106717     parent
46       631  109823     parent
47       632  109964     parent
48       633  106450     parent
49       634  108112     parent
50       635  108179     parent
51       636  107293     parent
52       637  109852     parent
53       638  109853     parent
54       639  109854     parent
55       640  109990     parent

In [41]:
os.listdir()

['make_intermediates.ipynb',
 'new_sungnam_network_internal_0809.net.xml',
 'signal_node_matching.xlsx',
 'sn_admin_tables',
 '~$signal_node_matching.xlsx',
 '~$교차로기반정보_(시범지역).xlsx',
 '교차로기반정보_(시범지역).xlsx']

In [42]:
# dfs = {'dayplan':dayplan, 'red_yel':red_yel, 'weekplan':weekplan, 'flows':flows}
# for df_name, df in dfs.items():
#     print(df_name)
#     assert set(df.CRSRD_ID).issubset(inter_nos)
#     inter_no_coincide = inter_nos == set(df.CRSRD_ID)
#     if not inter_no_coincide:
#         print(f"  inter_no's doesn't conicide.")
#         print(f"  missing inter_no's : {inter_nos - set(df.CRSRD_ID)}")

In [43]:
# venn3([set(dayplan.CRSRD_ID), set(red_yel.CRSRD_ID), set(weekplan.CRSRD_ID)], ('dayplan', 'redyel', 'weekplan'))
# plt.show()
# print(f'일간계획 테이블의 교차로 개수 : {len(set(dayplan.CRSRD_ID))}')
# print(f'황색적색 테이블의 교차로 개수 : {len(set(red_yel.CRSRD_ID))}')
# print(f'주간계획 테이블의 교차로 개수 : {len(set(weekplan.CRSRD_ID))}')
# CRSRD_IDs_plan = set(dayplan.CRSRD_ID) & set(red_yel.CRSRD_ID) & set(weekplan.CRSRD_ID)
# print(f'겹치는 교차로 개수 : {len(CRSRD_IDs_plan)}')
# print(f'겹치는 교차로 목록 : {sorted(CRSRD_IDs_plan)}')